In [60]:
import sys

import matplotlib.pyplot as plt
%matplotlib inline
import copy
import datetime
import pickle
import gzip
import os,glob
import time
import numpy as np
import pandas as pd
import operator

import plotly.plotly as py
import plotly.graph_objs as go

import numpy as np

#sys.path
from tqdm import tqdm
from tqdm import tnrange, tqdm_notebook

import regex as re
import datetime
import math
import time

from IPython.core.display import display,HTML
display(HTML("<style>.container { width:100% !important; }</style>"))  # to make the notebook use the entire width of the browser


In [2]:
# This code is the MongoConnection class from the Amaral lab LabTools folder.

from __future__ import print_function, unicode_literals
import sys
from pymongo import MongoClient


class MongoConnection(object):
    def __init__(self, cxnSettings, **kwargs):
        self.settings = cxnSettings
        self.mongoURI = self._constructURI()
        self.connect(**kwargs)
        self.ensure_index()

    def _constructURI(self):
        '''
        Construct the mongo URI
        '''
        mongoURI = 'mongodb://'
        #User/password handling
        if 'user'in self.settings and 'password' in self.settings:
            mongoURI += self.settings['user'] + ':' + self.settings['password']
            mongoURI += '@'
        elif 'user' in self.settings:
            print('Missing password for given user, proceeding without either')
        elif 'password' in self.settings:
            print('Missing user for given passord, proceeding without either')
        #Host and port
        try:
            mongoURI += self.settings['host'] + ':'
        except KeyError:
            print('Missing the hostname. Cannot connect without host')
            sys.exit()
        try:
            mongoURI += str(self.settings['port'])
        except KeyError:
            print('Missing the port. Substituting default port of 27017')
            mongoURI += str('27017')
        return mongoURI

    def connect(self, **kwargs):
        '''
        Establish the connection, database, and collection
        '''
        self.connection = MongoClient(self.mongoURI, **kwargs)
        #########
        try:
            self.db = self.connection[self.settings['db']]
        except KeyError:
            print("Must specify a database as a 'db' key in the settings file")
            sys.exit()
        #########
        try:
            self.collection = self.db[self.settings['collection']]
        except KeyError:
            print('Should have a collection.', end='')
            print('Starting a collection in database', end='')
            print(' for current connection as test.')
            self.collection = self.db['test']

    def tearDown(self):
        '''
        Closes the connection
        '''
        self.connection.close()

    def ensure_index(self):
        '''
        Ensures the connection has all given indexes.
        indexes: list of (`key`, `direction`) pairs.
            See docs.mongodb.org/manual/core/indexes/ for possible `direction`
            values.
        '''
        if 'indexes' in self.settings:
            for index in self.settings['indexes']:
                self.collection.ensure_index(index[0], **index[1])

In [3]:
merged_papers_settings = {
    "host": "chicago.chem-eng.northwestern.edu",
    "port": "27017",
    "db": "web_of_science_aux",
    "collection": "merged_papers",
    "user": "mongoreader",
    "password": "emptycoffeecup"
}

papers_con = MongoConnection(merged_papers_settings)


In [ ]:

lista_all_plos_UTs = pickle.load(open('../data/lista_all_plos_UTs.pkl', 'rb'))
new_lista_all_plos_UTs = ['000'+str(item) for item in lista_all_plos_UTs]
print (len(lista_all_plos_UTs))

lista_all_reference_UTs = pickle.load(open('../data/lista_all_reference_UTs.pkl', 'rb'))
print (len(lista_all_reference_UTs))






lista_UTs_plos_and_ref=new_lista_all_plos_UTs+ lista_all_reference_UTs
lista_UTs_plos_and_ref =  list(set(lista_UTs_plos_and_ref))
len(lista_UTs_plos_and_ref)   #2706287 without repetitions

In [24]:

def  get_keywords(list_UTs,  dict_ref_UT_list_keywords):
    
    # Retrieve the keywords for the list of UTs provided
    
    
    cont=0

    query = papers_con.collection.find({"UT":{"$in":list_UTs}},{"UT":1,"ID":1}, no_cursor_timeout=True)  # it returns an iterator (it gets empty after iterating over it once) # second {} to select the fields it returns, if i dont want them all


    for item in query:  # query (cursor) is an iterator (once i iterate over it once, it is empty), and every item is a dict

        UT=item["UT"]
        try:
            keywords= str(item['ID']).replace('[','').replace(']','').replace("'","")
        except KeyError:
            cont +=1
            keywords=""
  
        dict_ref_UT_list_keywords[UT] = keywords
#         print  (UT, keywords)
#         input()
        
        
        
    query.close()  # because i am using the no_cursor_timeout=True, i need also this, or cursor keeps waiting so ur resources are used up

            
    return  cont
    
#######################################



In [34]:

try:  
      
    dict_ref_UT_list_keywords = pickle.load(open('../data/dict_ref_UT_list_keywords_plos_papers.pkl', 'rb'))
    print ("read dict_ref_UT_list_keywords", len(dict_ref_UT_list_keywords))    
except:    
    dict_ref_UT_list_keywords ={}
    

 
cont_no_keywords=0
stop= len(new_lista_all_plos_UTs)
initial=len(dict_ref_UT_list_keywords)
delta=int(stop/100.)
final=initial + delta

while final-delta <=  stop:    
    print (" ",initial, final, "....",)

    partial_list=new_lista_all_plos_UTs[initial:final]  # slicing beyond the length of the list is NOT a problem

    cont_no_keywords += get_keywords(partial_list,  dict_ref_UT_list_keywords)

    with open('../data/dict_ref_UT_list_keywords_plos_papers.pkl', 'wb') as handle:
        pickle.dump(dict_ref_UT_list_keywords, handle, protocol = 2)   
        print ( len(dict_ref_UT_list_keywords), '../data/dict_ref_UT_list_keywords_plos_papers.pkl', "fraction papers without keyword so far", cont_no_keywords/float(len(dict_ref_UT_list_keywords)))        

        
     

    initial += delta
    final = initial +delta
    
print ("done.")
print (len(dict_ref_UT_list_keywords))


with open('../data/dict_ref_UT_list_keywords_plos_papers.pkl', 'wb') as handle:
        pickle.dump(dict_ref_UT_list_keywords, handle, protocol = 2)   
        print ( len(dict_ref_UT_list_keywords), '../data/dict_ref_UT_list_keywords_plos_papers.pkl', "fraction papers without keyword so far", cont_no_keywords/float(len(dict_ref_UT_list_keywords)))        

   

# started around 3:41pm (+2 iter)

read dict_ref_UT_list_keywords 4764
  4764 6352 ....
6352 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.014641057934508817
  6352 7940 ....
7940 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.021788413098236776
  7940 9528 ....
9528 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.025923593618807726
  9528 11116 ....
11116 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.03076646275638719
  11116 12704 ....
12704 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.034713476070528965
  12704 14292 ....
14292 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.036453960257486706
  14292 15880 ....
15880 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.03853904282115869
  15880 17468 ....
17468 ../dat

  101632 103220 ....
103220 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.0530517341600465
  103220 104808 ....
104808 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.05298259674833982
  104808 106396 ....
106396 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.05296251738787172
  106396 107984 ....
107984 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.05292450733441991
  107984 109572 ....
109572 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.05285109334501515
  109572 111160 ....
111160 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.052869737315581145
  111160 112748 ....
112748 ../data/dict_ref_UT_list_keywords_plos_papers.pkl fraction papers without keyword so far 0.05302089615780324
  112748 114336 ....
114336 ../data/dict_

In [35]:
dict_ref_UT_list_keywords

{'000207444600001': '',
 '000207445300008': '',
 '000207446000005': '',
 '000207455300012': '',
 '000207455300019': '',
 '000207455700009': '',
 '000207459400009': '',
 '000254928800015': 'BODY-MASS INDEX, CARE COSTS, UNITED-STATES, FUTURE BURDEN, RISK-FACTORS, SMOKING, DISEASE, IMPACT, INTERVENTIONS, NETHERLANDS',
 '000257105600004': 'EMERGENCY OBSTETRIC CARE, PEDIATRIC-SURGERY, TRAUMA-CARE, COUNTRIES, SERVICES, NEED, PROGRAM, AREA',
 '000259783100021': 'A VIRUSES, ADAMANTANE RESISTANCE, HEMAGGLUTININ GENE, H3N2 VIRUSES, EVOLUTION, SPREAD, REASSORTMENT, MORTALITY, WORLDWIDE, SELECTION',
 '000260586600028': '',
 '000260586600030': '',
 '000260795500028': '',
 '000261558700005': '',
 '000261558700028': '',
 '000261642400030': '',
 '000261806900002': '',
 '000261807000003': 'CHRONIC HELMINTH INFECTIONS, TROPICAL DISEASES, POLYMORPHISMS, IMPACT',
 '000263288000016': '',
 '000263288200008': '',
 '000263301100009': 'ANTIGEN-CAPTURE ELISA, VIRUS-INFECTION, HEMORRHAGIC-FEVER, DISEASE SEVERITY

In [64]:
dict_keyword_tot_occurrences={}
list_num_keywords=[]
for llave in dict_ref_UT_list_keywords:
#     if 'BEHAVIOR' in dict_ref_UT_list_keywords[llave]:
#         print (llave, dict_ref_UT_list_keywords[llave])
#         input()
    list_keywords = dict_ref_UT_list_keywords[llave].split(", ")
    list_num_keywords.append(len(list_keywords))
    if dict_ref_UT_list_keywords[llave] != '':
        
        for item in list_keywords:
            try:
                dict_keyword_tot_occurrences[item] +=1
            except KeyError:
                dict_keyword_tot_occurrences[item] = 1
#         print (dict_ref_UT_list_keywords[llave], list_keywords)
#         input()
    else:
        print (llave, dict_ref_UT_list_keywords[llave])
        input()

000207444600001 

000207445300008 

000207446000005 

000207455300012 

000207455300019 

000207455700009 

000207459400009 

000260586600028 

000260586600030 

000260795500028 

000261558700005 

000261558700028 

000261642400030 


KeyboardInterrupt: 

In [63]:
print (np.mean(list_num_keywords), len(list_num_keywords))


data = [go.Histogram(x=list_num_keywords)]

py.iplot(data, filename='basic histogram')

8.73611102366 158813


/home/staff/julia/.pyenv/versions/3.6.4/envs/psy/lib/python3.6/site-packages/plotly/plotly/plotly.py:224: UserWarning:

Woah there! Look at all those points! Due to browser limitations, the Plotly SVG drawing functions have a hard time graphing more than 500k data points for line charts, or 40k points for other types of charts. Here are some suggestions:
(1) Use the `plotly.graph_objs.Scattergl` trace object to generate a WebGl graph.
(2) Trying using the image API to return an image instead of a graph URL
(3) Use matplotlib
(4) See if you can create your visualization with fewer data points

If the visualization you're using aggregates points (e.g., box plot, histogram, etc.) you can disregard this warning.



In [48]:
sorted_dict = sorted(dict_keyword_tot_occurrences.items(), key=operator.itemgetter(1)) #dict_keyword_tot_occurrences
sorted_dict[::-1]

[('EXPRESSION', 13531),
 ('GENE-EXPRESSION', 6923),
 ('IDENTIFICATION', 5992),
 ('DISEASE', 5807),
 ('ACTIVATION', 5644),
 ('IN-VIVO', 5244),
 ('CELLS', 5056),
 ('PROTEIN', 5036),
 ('IN-VITRO', 4910),
 ('INFECTION', 4579),
 ('MICE', 4372),
 ('GENE', 4279),
 ('RISK', 3827),
 ('EVOLUTION', 3759),
 ('CANCER', 3604),
 ('GROWTH', 3526),
 ('ESCHERICHIA-COLI', 3245),
 ('MODEL', 3133),
 ('POPULATION', 3024),
 ('DIFFERENTIATION', 2985),
 ('PREVALENCE', 2960),
 ('ASSOCIATION', 2838),
 ('OXIDATIVE STRESS', 2764),
 ('MECHANISMS', 2619),
 ('CHILDREN', 2546),
 ('RISK-FACTORS', 2426),
 ('MORTALITY', 2389),
 ('SURVIVAL', 2382),
 ('APOPTOSIS', 2323),
 ('THERAPY', 2288),
 ('UNITED-STATES', 2260),
 ('DIVERSITY', 2240),
 ('BREAST-CANCER', 2229),
 ('RECEPTOR', 2211),
 ('INFLAMMATION', 2171),
 ('RESPONSES', 2168),
 ('BRAIN', 2163),
 ('RESISTANCE', 2137),
 ('PROTEINS', 2062),
 ('METAANALYSIS', 2049),
 ('SYSTEM', 2007),
 ('INHIBITION', 1997),
 ('DYNAMICS', 1981),
 ('BINDING', 1915),
 ('HEALTH', 1905),
 ('MANA

In [49]:
for key in sorted(dict_keyword_tot_occurrences):
    print (key, dict_keyword_tot_occurrences[key])

"(3H)J(NC)" 2
"1-ACETOXYCHAVICOL ACETATE" 1
"2,2-DIFLUORODEOXYCYTIDINE" 2
"2,3-CYCLIC NUCLEOTIDE 3-PHOSPHODIESTERASE" 1
"2,4,5,2,4,5-HEXACHLOROBIPHENYL" 1
"2,4-BNA(NC)" 1
"2,5-DIHYDROXY-4,3-DI(BETA-D-GLUCOPYRANOSYLOXY)-TRANS-STILBENE" 1
"2,5-OLIGOADENYLATE SYNTHETASE 1B" 1
"2,5-OLIGOADENYLATE SYNTHETASE" 1
"2,7-DICHLOROFLUORESCIN DIACETATE" 1
"2,7-DICHLOROFLUORESCIN" 1
"2-5-OLIGOADENYLATE SYNTHETASE GENE" 1
"2-5-OLIGOADENYLATE SYNTHETASE" 1
"2-5-RNA LIGASE" 1
"2-DEOXYMUGINEIC ACID" 1
"2-HYDROXYCHALCONES" 1
"3 ADENYLATION" 2
"3 END FORMATION" 1
"3 END" 6
"3 EXONUCLEASE" 1
"3 NONCODING REGION" 1
"3 NONTRANSLATED REGION" 1
"3 PROCESSING ENDORIBONUCLEASE" 3
"3 REGION" 1
"3 TERMINI" 4
"3 UNTRANSLATED REGION" 11
"3 UNTRANSLATED REGIONS" 22
"3 URIDYLATION" 1
"3 UTR" 1
"3 UTRS" 1
"3(2),5-BISPHOSPHATE NUCLEOTIDASE" 1
"3,3-DIINDOLYLMETHANE DIM" 2
"3,3-DIINDOLYLMETHANE" 2
"3,5-CYCLIC-AMP CAMP PHOSPHODIESTERASE" 1
"3,5-HYDROXYLASE" 1
"3-5 EXONUCLEASE ACTIVITY" 1
"3-5 EXONUCLEOLYSIS" 1
"3-AZIDO-3-D

A GENE 3
A GENE FAMILY 1
A GENE PROMOTER 1
A GENE-EXPRESSION 2
A H1N1 67
A H1N1 2009 1
A H1N1 VACCINE 1
A H1N1 VIRUS 55
A H1N1 VIRUSES 1
A H3N2 1
A H3N2 EPIDEMIC 1
A H3N2 VIRUSES 3
A H5N1 24
A H5N1 INFECTION 1
A H5N1 VIRUS 20
A H5N1 VIRUSES 4
A H7N9 2
A H7N9 VIRUS 16
A INFECTION 1
A ISOFORM 1
A KINASE 4
A LEVELS 2
A LIGANDS 2
A LIGHT 1
A LIGHT-CHAIN 1
A MCRA GENES 2
A MSRA 1
A MUTANT MICE 1
A NEURONS 1
A NEUROTOXIN 2
A NUCLEOSOMES 1
A OSPA 2
A OVEREXPRESSION 1
A PHOSPHORYLATION SITE 1
A PHOTORECEPTORS 1
A PROGENITOR TOXINS 1
A PROTEIN 2
A RECEPTOR 7
A RECEPTORS 11
A REDUCTASE 1
A REDUCTASE INHIBITORS 3
A ROTAVIRUS 1
A RPA 1
A SAA 1
A SAA PROTEIN 1
A SCAVENGER RECEPTOR 1
A SCAVENGER RECEPTORS 1
A SPERMATOGONIA 2
A STRAINS 1
A STREPTOCOCCAL INFECTIONS 2
A SUBREGION 1
A SUBTYPE H5N1 1
A SUPERFAMILY 1
A SYNTHETASE 1
A SYNTHETASE ACSA 1
A TARGET 1
A TOXIN 1
A TRANSMEMBRANE DOMAIN 1
A TREATMENT 2
A VACCINE 5
A VIRAL HEMAGGLUTININS 1
A VIRUS 209
A VIRUS H5N1 4
A VIRUS HEMAGGLUTININ 3
A VIRUS 

ACUTE MEDICAL ILLNESS 2
ACUTE MEGAKARYOBLASTIC LEUKEMIA 4
ACUTE MEGAKARYOCYTIC LEUKEMIA 2
ACUTE MELIOIDOSIS 1
ACUTE MENTAL STRESS 2
ACUTE MESENTERIC ISCHEMIA 1
ACUTE MEVINPHOS INTOXICATION 2
ACUTE MICROINJECTIONS 1
ACUTE MONOHEMISPHERIC STROKE 1
ACUTE MORPHINE 1
ACUTE MOUNTAIN-SICKNESS 14
ACUTE MURINE COLITIS 1
ACUTE MYELOBLASTIC-LEUKEMIA 1
ACUTE MYELOCYTIC-LEUKEMIA 1
ACUTE MYELOGENOUS LEUKEMIA 48
ACUTE MYELOID LEUKEMIAS 1
ACUTE MYELOID-LEUKEMIA 284
ACUTE MYOCARDIAL-INFARCTION 283
ACUTE MYOCARDIAL-INFARCTION/ 2
ACUTE NECROTIZING ENCEPHALOPATHY 4
ACUTE NECROTIZING PANCREATITIS 6
ACUTE NEPHROCALCINOSIS 1
ACUTE NONCONVULSIVE SEIZURES 1
ACUTE NOXIOUS-STIMULATION 1
ACUTE OPIOID DEPENDENCE 1
ACUTE OPTIC NEURITIS 1
ACUTE ORGAN TOXICITY 1
ACUTE OSTEOMYELITIS 1
ACUTE OTITIS-MEDIA 34
ACUTE OXALATE NEPHROPATHY 2
ACUTE PAIN 1
ACUTE PARALYSIS VIRUS 8
ACUTE PHASE 1
ACUTE PHENYLALANINE/TYROSINE DEPLETION 2
ACUTE PHYSICAL-EXERCISE 1
ACUTE PHYSIOLOGY 13
ACUTE PHYSIOLOGY SCORE 2
ACUTE PLACENTAL INFLAMMA

AGGRESSIVE BEHAVIOR 1
AGGRESSIVE BREAST-CANCER 1
AGGRESSIVE COMPETITION 1
AGGRESSIVE DISEASE 1
AGGRESSIVE FIBROMATOSIS 2
AGGRESSIVE LYMPHOMA 1
AGGRESSIVE LYMPHOMAS 3
AGGRESSIVE MIMICRY 2
AGGRESSIVE MYELOID-LEUKEMIA 1
AGGRESSIVE PERIODONTITIS 17
AGGRESSIVE POSTERIOR RETINOPATHY 3
AGGRESSIVE REGIMENS 1
AGGRESSIVE SIGNAL 1
AGGRESSIVE TUMOR-GROWTH 1
AGGRESSIVE-BEHAVIOR 37
AGGRESSIVENESS 11
AGGRESSIVENESS LOCI 1
AGGRUS 1
AGGRUS/PODOPLANIN 1
AGILE GIBBONS 1
AGILENT MICROARRAY 1
AGILITY 1
AGINCOURT HEALTH 4
AGING APPEARANCE 1
AGING BRAIN 14
AGING DROSOPHILA 2
AGING GENOMIC RESOURCES 1
AGING HIPPOCAMPUS 1
AGING HUMAN BRAIN 2
AGING HUMAN HEART 2
AGING KIDNEY 4
AGING LUNG 1
AGING MALE 1
AGING MEN 3
AGING MICE 1
AGING MIND 1
AGING POPULATION 2
AGING PRIMATES 4
AGING PROCESS 2
AGING PROJECT 5
AGING RAT-HEART 1
AGING RATS 2
AGING RESEARCH 3
AGING RETINA 1
AGING ROS 1
AGING SKIN 1
AGING-ASSOCIATED ALTERATION 1
AGING-ASSOCIATED PHENOTYPES 3
AGING-RELATED CHANGES 1
AGITATION 4
AGITATION-SEDATION SCALE

AL-AMYLOIDOSIS 1
AL-MUNAWARAH PROVINCE 1
AL. CIRCADIAN VARIATION 1
ALA 2
ALABAMA 1
ALABAMA BEACHES 1
ALABAMICA 1
ALACHLOR 1
ALACRANES REEF 1
ALAFENAMIDE 1
ALAGILLE SYNDROME 2
ALAGILLE-SYNDROME 12
ALALUNGA 1
ALAMAR BLUE 1
ALAMAR BLUE ASSAY 1
ALAMAR-BLUE 1
ALAMEDA COUNTY 3
ALAMEDA-COUNTY 1
ALAMETHICIN 3
ALAMOSAURUS-SANJUANENSIS 1
ALANINE 1
ALANINE AMINOPEPTIDASE 1
ALANINE AMINOTRANSFERASE 14
ALANINE AMINOTRANSFERASE ACTIVITY 1
ALANINE AMINOTRANSFERASE LEVEL 2
ALANINE AMINOTRANSFERASE LEVELS 5
ALANINE DIPEPTIDE 1
ALANINE LIGASE 1
ALANINE METABOLISM 1
ALANINE RACEMASE 3
ALANINE SCANNING MUTAGENESIS 1
ALANINE SUBSTITUTION 1
ALANINE SUBSTITUTIONS 1
ALANINE TRANSAMINASE-ACTIVITY 1
ALANINE-AMINOTRANSFERASE 1
ALANINE-BASED PEPTIDES 1
ALANINE-GLYOXYLATE AMINOTRANSFERASE 1
ALANINE-GLYOXYLATE AMINOTRANSFERASE-2 1
ALANINE-RICH 2
ALANINE-RICH KINASE 2
ALANINE-RICH PROTEIN 1
ALANINE-SCANNING MUTAGENESIS 4
ALANINEGLYOXYLATE AMINOTRANSFERASE 3
ALANYL-D-ALANINE 2
ALANYL-LIPOTEICHOIC ACID 3
ALARM 1
ALARM

...

TYPE-1 R5 ENVELOPES 1
TYPE-1 REACTION 1
TYPE-1 REACTIONS 1
TYPE-1 RECEPTOR 10
TYPE-1 RECEPTOR ANTAGONIST 1
TYPE-1 RECEPTOR ANTAGONISTS 1
TYPE-1 RECEPTOR EXPRESSION 2
TYPE-1 RECOMBINATION 1
TYPE-1 REPEAT TSR 1
TYPE-1 REPEATS 3
TYPE-1 REPLICATION 12
TYPE-1 REV 1
TYPE-1 REVERSAL REACTIONS 1
TYPE-1 REVERSE TRANSCRIPTION 1
TYPE-1 REVERSE-TRANSCRIPTASE 10
TYPE-1 RNA 11
TYPE-1 RYANODINE RECEPTOR 1
TYPE-1 RYANODINE RECEPTORS 1
TYPE-1 SEROCONVERSION 4
TYPE-1 STRAINS 1
TYPE-1 SUBTYPE 3
TYPE-1 SUBTYPE-C 3
TYPE-1 SUBTYPES 5
TYPE-1 TAT 4
TYPE-1 TAT TRANSACTIVATOR 1
TYPE-1 TAX 2
TYPE-1 TAX PROTEIN 1
TYPE-1 THYMIDINE KINASE 3
TYPE-1 TRANSCRIPTION 2
TYPE-1 TRANSCYTOSIS 2
TYPE-1 TRANSMISSION 1
TYPE-1 TROPISM 3
TYPE-1 VARIANT 1
TYPE-1 VARIANTS 3
TYPE-1 VIF 3
TYPE-1 VIRIONS 2
TYPE-1 VIRUS 1
TYPE-1 VPR 4
TYPE-1 VPU 2
TYPE-11 1
TYPE-15 1
TYPE-16 15
TYPE-16 DNA 3
TYPE-16 E1 1
TYPE-16 E6 4
TYPE-16 E7 1
TYPE-16 E7 ONCOPROTEIN 3
TYPE-16 L1 2
TYPE-16 VARIANTS 2
TYPE-18 1
TYPE-19 INFECTION 1
TYPE-1A RECEPTOR 1
T

VANCOMYCIN-INTERMEDIATE STRAINS 1
VANCOMYCIN-RESISTANT 2
VANCOMYCIN-RESISTANT ENTEROCOCCI 5
VANCOMYCIN-RESISTANT ENTEROCOCCUS 6
VANCOUVER 1
VANCOUVER-ISLAND 20
VANDA 1
VANDEAE 1
VANDERPOL OSCILLATOR 1
VANDERWAALS FORCES 1
VANDERWART PICTURES 3
VANDETANIB PLUS DOCETAXEL 2
VANETS 1
VANGL1 1
VANGL2 2
VANGL2 MUTATIONS 1
VANHOEFFENI 1
VANILLIN 1
VANILLOID 1 TRPV1 1
VANILLOID CAPSAICIN RECEPTORS 1
VANILLOID RECEPTOR 9
VANILLOID RECEPTOR TRPV1 4
VANILLOID RECEPTOR-1 6
VANILLOID RECEPTOR-1 TRPV1 1
VANILLOID RECEPTORS 6
VANILLOID VR1 RECEPTORS 1
VANILLYL BENZYL ETHER 1
VANISHING DISEASE 3
VANISHING WHITE-MATTER 6
VANTAGE POINT 1
VANUATU 2
VAPA 1
VAPB 1
VAPB INTERACTS 1
VAPOR 3
VAPOR COLUMN ABUNDANCE 1
VAPOR DIFFUSION 2
VAPOR EXTRACT 2
VAPOR GENERATION 2
VAPOR-DEPOSITION 1
VAPOR-PHASE 1
VAPOR-PRESSURE DEFICIT 5
VAPORS 3
VAQUITA PHOCOENA-SINUS 1
VAR ATROSEPTICA 1
VAR CANIS 1
VAR GATTII MENINGITIS 1
VAR GENE 6
VAR GENE-EXPRESSION 2
VAR GENE-TRANSCRIPTION 3
VAR GENES 16
VAR. CHIA 1
VAR. CICLA EXTRA

VISUAL OBJECT RECOGNITION 2
VISUAL ODDBALL TASK 1
VISUAL ONSETS 1
VISUAL ORIENTATION 2
VISUAL OUTCOMES 1
VISUAL PATHWAY 8
VISUAL PATHWAYS 5
VISUAL PERCEPTION 1
VISUAL PERFORMANCE 5
VISUAL PERSISTENCE 1
VISUAL PERSPECTIVE 1
VISUAL PERSPECTIVE-TAKING 2
VISUAL PIGMENT 3
VISUAL PIGMENT COMPOSITION 1
VISUAL PIGMENTS 32
VISUAL POSITION-INFORMATION 1
VISUAL PREDATION RISK 1
VISUAL PREFERENCE 1
VISUAL PRIOR ENTRY 1
VISUAL PRIOR-ENTRY 1
VISUAL PROCESSING DEFICITS 1
VISUAL PROPERTIES 2
VISUAL PROSTHESIS 1
VISUAL PSYCHOPHYSICS 1
VISUAL RECEPTIVE-FIELDS 3
VISUAL RECOGNITION 1
VISUAL RECOGNITION MEMORY 1
VISUAL RECOVERY 4
VISUAL REFERENCE 1
VISUAL RESOLUTION 1
VISUAL RESPONSE PROPERTIES 2
VISUAL RESPONSES 4
VISUAL RHYTHMS 2
VISUAL SALTATION 1
VISUAL SCANPATH 1
VISUAL SCENES 2
VISUAL SCORES 1
VISUAL SELECTIVE ATTENTION 5
VISUAL SELF-RECOGNITION 3
VISUAL SELF-REPRESENTATION 1
VISUAL SENSATIONS 1
VISUAL SENSITIVITY 1
VISUAL SETS 1
VISUAL SEXUAL STIMULI 2
VISUAL SIGNAL-DETECTION 1
VISUAL SIZE CUES 1
VI

WILD FROGS 2
WILD GELADAS 1
WILD GIRAFFES 1
WILD GOURD 1
WILD HORSES 2
WILD HOSTS 1
WILD JAPANESE MACAQUES 1
WILD LENTILS 1
WILD MAMMALS 2
WILD MEAT 1
WILD MICE 3
WILD MOUNTAIN GORILLAS 1
WILD MOUSE 1
WILD MUSHROOMS 1
WILD MUSTARD 1
WILD OLIVES 1
WILD ORANGUTANS 3
WILD PIGS 1
WILD PINK SALMON 1
WILD PLANTS 3
WILD POLIOVIRUS 4
WILD POLLINATORS 4
WILD POPULATION 2
WILD POPULATIONS 16
WILD PRIMATES 3
WILD RABBIT 1
WILD RABBITS 3
WILD RADISH 5
WILD RATS 1
WILD REINDEER 4
WILD RELATIVES 18
WILD RODENT 1
WILD RODENTS 5
WILD RUMINANTS 2
WILD SALMON 5
WILD SEA-TROUT 1
WILD SHEEP 1
WILD SMALL MAMMALS 1
WILD STOCKS 1
WILD SUGARCANE 1
WILD SUNFLOWERS 1
WILD TETRAPLOID WHEAT 1
WILD THOMAS LANGURS 1
WILD TOBACCO 2
WILD TOMATO 2
WILD TOMATOES 4
WILD TURKEY HENS 1
WILD TURKEYS 1
WILD VARIANT 1
WILD VEGETABLES 1
WILD WATERFOWL 2
WILD WATERMELON 1
WILD WHEAT 1
WILD WHEATS 3
WILD WOLVES 1
WILD YEASTS 1
WILD ZEBRAFISH 1
WILD-CAUGHT 2
WILD-DERIVED MICE 1
WILD-RICE 4
WILD-TYPE 141
WILD-TYPE ADENOVIRUS 2
WI

WOMENS INTERAGENCY HIV 9
WOMENS KNOWLEDGE 2
WOMENS MATH PERFORMANCE 4
WOMENS PERCEPTIONS 1
WOMENS PREFERENCES 5
WOMENS REPORTS 1
WOMENS RISK 1
WOMENS STATUS 1
WOMENS UNDERREPRESENTATION 2
WOMENS VOICES 1
WOMENS WORK 1
WOMENS-HEALTH 2
WONDERWERK CAVE 1
WOOD 26
WOOD ANATOMY 1
WOOD ANTS 6
WOOD BISON 2
WOOD CHEMISTRY 1
WOOD CHIPS 1
WOOD CREOSOTE 1
WOOD DECAY 3
WOOD DENSITY 11
WOOD DUCKS 2
WOOD DUST 1
WOOD EXTRACTS 1
WOOD FORMATION 7
WOOD FROG 3
WOOD FROGS 3
WOOD MICE 3
WOOD MOUSE 3
WOOD NEMATODE 8
WOOD PRODUCTION 2
WOOD PROPERTY TRAITS 3
WOOD QUALITY 1
WOOD SAWDUST 1
WOOD SMOKE 2
WOOD SMOKE EXPOSURE 1
WOOD SPECIFIC-GRAVITY 2
WOOD STORK 1
WOOD STRUCTURE 2
WOOD-BORING BIVALVES 3
WOOD-BORING INSECTS 1
WOOD-DECAYING FUNGI 2
WOOD-FEEDING COCKROACHES 1
WOOD-FORMING TISSUES 1
WOOD-HARVEST 1
WOOD-LJUNGDAHL PATHWAY 1
WOOD-MASON 1
WOOD-ROTTING FUNGI 1
WOODCHUCK 1
WOODCHUCK HEPATITIS 1
WOODCHUCK HEPATITIS-VIRUS 1
WOODCHUCK MODEL 1
WOODCREEPERS 1
WOODED MEADOWS 1
WOODED PASTURES 1
WOODEN HAND 2
WOODEN

In [53]:
from nltk.corpus import wordnet

In [55]:
syns = wordnet.synsets("program")

NameError: name 'synsets' is not defined

In [56]:
len(dict_keyword_tot_occurrences)

205970